In [1]:
import pandas as pd
from sklearn.externals import joblib
from sklearn.ensemble import RandomForestClassifier
from sklearn import tree
from sklearn import ensemble
import datetime
import numpy as np
import pandas as pd
import graphviz 
import pydotplus
from pandas.tseries.offsets import Hour
import traceback
import os
from dateutil.relativedelta import relativedelta

C:\ProgramData\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d


In [2]:
#Prepare to load Data Frames with SQLAlchemy
from sqlalchemy import create_engine, sql
import pymysql
pymysql.install_as_MySQLdb()

#from config import remote_db_endpoint, remote_db_port
#from config import remote_gwsis_dbname, remote_gwsis_dbuser, remote_gwsis_dbpwd

# AWS Database Info - Put in Config file!
remote_db_endpoint = 'gwcodingbootcamp.cr0gccbv4ylw.us-east-2.rds.amazonaws.com'
remote_db_port = '3306'
remote_gwsis_dbname = 'bikeshare_db'
remote_gwsis_dbuser = 'root'
remote_gwsis_dbpwd = 'braddocks'
# ADD PASSWORD HERE FOR AWS DATABASE - i know i shouldn't put it, 
#but couldn't get separate users to 

In [3]:
# AWS Database Connection
engine = create_engine(f"mysql://{remote_gwsis_dbuser}:{remote_gwsis_dbpwd}@{remote_db_endpoint}:{remote_db_port}/{remote_gwsis_dbname}")
# Create a remote database engine connection
conn = engine.connect()

In [4]:
print(conn)

In [8]:
# Get and Adjust Data

START_DATE = datetime.date.today() - relativedelta(months=26)
END_DATE = datetime.date.today()
station_id = 32407


data_list = []
start = pd.to_datetime(START_DATE, infer_datetime_format=True)
end = pd.to_datetime(END_DATE, infer_datetime_format=True)
# Create empty DateTimeIndex with frequency of five minutes, and assign it
# to an empty series.
# "5T" is five minutes.
dti = pd.date_range(0, -1, freq="5T")
data = pd.Series(None, index=dti)
    
bike_counts = pd.read_sql(f"SELECT time, num_bikes, num_empty_docks FROM bikeshare WHERE time BETWEEN '{start}' AND '{end}' AND term_num = '{station_id}'", \
                              conn)  


In [34]:
print(start)
print(START_DATE)
print(END_DATE)

2017-03-14 00:00:00
2017-03-14
2019-05-14


In [10]:
bike_counts.head(25)

time  num_bikes  num_empty_docks
0  2019-04-03 21:14:00          7                7
1  2019-04-03 21:17:00          7                7
2  2019-04-03 21:20:00          7                7
3  2019-04-03 21:23:00          7                7
4  2019-04-03 21:26:00          7                7
5  2019-04-03 21:29:00          7                7
6  2019-04-03 21:32:00          7                7
7  2019-04-03 21:35:00          7                7
8  2019-04-03 21:38:00          7                7
9  2019-04-03 21:41:00          7                7
10 2019-04-03 21:44:00          7                7
11 2019-04-03 21:47:00          7                7
12 2019-04-03 21:50:00          7                7
13 2019-04-03 21:53:00          7                7
14 2019-04-03 21:56:00          7                7
15 2019-04-03 21:59:00          7                7
16 2019-04-03 22:02:00          7                7
17 2019-04-03 22:05:00          7                7
18 2019-04-03 22:08:00          7                7
19 2019-04-03 22:11:00          7                7
20 2019-04-03 22:14:00          7                7
21 2019-04-03 22:17:00          7                7
22 2019-04-03 22:20:00          7                7
23 2019-04-03 22:23:00          7                7
24 2019-04-03 22:26:00          7                7

In [18]:
for bike_count in bike_counts.itertuples():
        # Do not insert counts with no bikes or spaces (inactive stations).
        if not (bike_count[2] == 0 and bike_count[3] == 0):
            ts = pd.to_datetime(bike_count[1], infer_datetime_format=True)
            # Round the timestamp to the nearest five minute mark.
            ts += datetime.timedelta(seconds=150)
            ts = ts.replace(
                minute=(ts.minute - (ts.minute % 5)), second=0, microsecond=0)

            # A status of np.nan means the station is neither full nor empty.
            status = np.nan
            if bike_count[2] == 0:
                status = "empty"
            elif bike_count[3] == 0:
                status = "full"

            # Create index with only one entry, ts.
            index = pd.date_range(ts, ts, freq="5T")

            data_list.append(pd.Series(status, index=index))

In [19]:
print(data_list)

[2019-04-03 21:15:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:15:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:20:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:25:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:25:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:30:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:30:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:35:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:40:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:40:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:45:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:45:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:50:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:55:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 21:55:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 22:00:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 22:00:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 22:05:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 22:10:00   NaN
Freq: 5T, dtype: float64, 2019-04-03 

In [23]:
    if len(data_list) > 0:
        data = pd.concat(data_list)

In [27]:
data.head(25)

2019-04-03 21:15:00    NaN
2019-04-03 21:15:00    NaN
2019-04-03 21:20:00    NaN
2019-04-03 21:25:00    NaN
2019-04-03 21:25:00    NaN
2019-04-03 21:30:00    NaN
2019-04-03 21:30:00    NaN
2019-04-03 21:35:00    NaN
2019-04-03 21:40:00    NaN
2019-04-03 21:40:00    NaN
2019-04-03 21:45:00    NaN
2019-04-03 21:45:00    NaN
2019-04-03 21:50:00    NaN
2019-04-03 21:55:00    NaN
2019-04-03 21:55:00    NaN
2019-04-03 22:00:00    NaN
2019-04-03 22:00:00    NaN
2019-04-03 22:05:00    NaN
2019-04-03 22:10:00    NaN
2019-04-03 22:10:00    NaN
2019-04-03 22:15:00    NaN
2019-04-03 22:15:00    NaN
2019-04-03 22:20:00    NaN
2019-04-03 22:25:00    NaN
2019-04-03 22:25:00    NaN
dtype: object

In [28]:
data_list = []
outages = pd.read_sql(f"SELECT Status, Start, End FROM historic_cabioutage WHERE `Terminal Number` = '{station_id}' AND Start >= '{start}' AND End <= '{end}'", \
                              conn)  

In [30]:
# Merge each outage into dataframe.
for outage in outages.itertuples():
    ostart = pd.to_datetime(outage[2], infer_datetime_format=True)
    ostart += datetime.timedelta(seconds=150)
    ostart = ostart.replace(
        minute=(ostart.minute - (ostart.minute % 5)),
        second=0, microsecond=0)
    oend = pd.to_datetime(outage[3], infer_datetime_format=True)
    oend += datetime.timedelta(seconds=150)
    oend = oend.replace(
        minute=(oend.minute - (oend.minute % 5)),
        second=0, microsecond=0)

    index = pd.date_range(ostart, oend, freq="5T")

    data_list.append(pd.Series(outage[1], index=index))

outage_data = pd.concat(data_list)

outage_data = outage_data.groupby(outage_data.index).first()


In [33]:
outage_data.head(250)

2018-09-06 10:05:00                    empty
2018-09-19 15:20:00               near empty
2018-09-19 15:25:00               near empty
2018-09-19 15:30:00               near empty
2018-09-19 15:35:00               near empty
2018-09-19 15:40:00               near empty
2018-09-19 15:45:00               near empty
2018-09-19 15:50:00               near empty
2018-09-19 15:55:00               near empty
2018-09-19 16:00:00               near empty
2018-09-19 16:05:00               near empty
2018-09-19 16:10:00               near empty
2018-09-19 16:15:00               near empty
2018-09-19 16:20:00               near empty
2018-09-19 16:25:00               near empty
2018-09-19 16:30:00               near empty
2018-09-19 16:35:00               near empty
2018-09-19 16:40:00               near empty
2018-09-19 16:45:00               near empty
2018-09-19 16:50:00               near empty
2018-09-19 16:55:00               near empty
2018-09-19 17:00:00               near empty
2018-09-19

In [37]:
query_outage_start = sql.text(
            "SELECT MIN(start) FROM historic_cabioutage "
            "WHERE `Terminal Number` = :station_id")
outage_data_start = conn.execute(
    query_outage_start, station_id=station_id).fetchone()[0]
query_outage_end = sql.text(
    "SELECT MAX(end) FROM historic_cabioutage "
    "WHERE `Terminal Number` = :station_id")
outage_data_end = conn.execute(
    query_outage_end, station_id=station_id).fetchone()[0]  

In [39]:
outage_data_start = pd.to_datetime(
            outage_data_start, infer_datetime_format=True)
outage_data_end = pd.to_datetime(
    outage_data_end, infer_datetime_format=True)

range_start = outage_data_start if outage_data_start > start else start
range_end = outage_data_end if outage_data_end < end else end

range_start = range_start.replace(
    minute=(range_start.minute - (range_start.minute % 5)),
    second=0, microsecond=0)
range_end = range_end.replace(
    minute=(range_end.minute - (range_end.minute % 5)),
    second=0, microsecond=0)

How do we make this read 'available'

In [40]:
  # Add NaN for those times when the station is not full or empty.
outage_data = outage_data.reindex(pd.date_range(
    range_start, range_end, freq="5T"))

# Remove any timestamps from outage_data that are in the bike_count
# data.
unique = outage_data.index.difference(data.index)
outage_data = outage_data.reindex(unique)

In [41]:
if outage_data is not None:
        data = pd.concat([data, outage_data])

# Remove any remaining stray duplicates.
data = data.groupby(data.index).first()

data.sort_index(inplace=True)

In [ ]:
# if(balance == "empty"):
#         df_empty = s[s == "empty"]
#         df_not_empty = s[s != "empty"]

#         return pd.concat([
#             df_not_empty.sample(len(df_empty)),
#             df_empty])
#     elif(balance == "full"):
#         df_full = s[s == "full"]
#         df_not_full = s[s != "full"]

#         return pd.concat([
#             df_not_full.sample(len(df_full)),
#             df_full])

In [47]:
 # Ensure shuffling.
data = data.iloc[np.random.permutation(len(data))]

X = []
yempty = []
yfull = []

#     weather_isd = pd.read_sql_query(
#         "SELECT * FROM weather_isd", db_engine, index_col="ts")

weather = pd.read_sql_query(
    "SELECT * FROM hourly_weather", conn, index_col="ts")

#     weather = pd.concat([weather_isd, weather])

weather.index = weather.index.tz_localize(None)

# Get rid of duplicates
weather = weather.groupby(level=0).first()

weather = weather.asfreq(Hour(), method="pad")

no_weather_count = 0

for row in data.iteritems():

    hour = row[0].replace(
        minute=0, second=0, microsecond=0, tzinfo=None)

    try:
        temp_hour = hour
        temp = float(weather.loc[temp_hour].temp)

        while pd.isnull(temp):
            temp_hour = temp_hour - datetime.timedelta(hours=1)
            temp = float(weather.loc[temp_hour].temp)

        precip_hour = hour
        precip = float(weather.loc[hour].precip)

        while pd.isnull(precip):
            precip_hour = precip_hour - datetime.timedelta(hours=1)
            precip = float(weather.loc[precip_hour].precip)

        features = [
            (1 if row[0].dayofweek == 0 else 0),
            (1 if row[0].dayofweek == 1 else 0),
            (1 if row[0].dayofweek == 2 else 0),
            (1 if row[0].dayofweek == 3 else 0),
            (1 if row[0].dayofweek == 4 else 0),
            (1 if row[0].dayofweek == 5 else 0),
            (1 if row[0].dayofweek == 6 else 0),
            float(((row[0].hour * 60) + row[0].minute)) / 1440.0,
            float(row[0].month) / 12.0,
            temp / 50.0,
            precip / 15.0
        ]

        X.append(features)
        yempty.append(1 if row[1] == "empty" else 0)
        yfull.append(1 if row[1] == "full" else 0)
    except KeyError as ex:
        no_weather_count += 1

print("Weather not found for", no_weather_count, "rows.")

Weather not found for 587 rows.


In [90]:
weather.describe()

temp        precip
count  29425.000000  29338.000000
mean      14.822117      0.098158
std        9.930395      0.725659
min      -12.800000      0.000000
25%        6.700000      0.000000
50%       15.000000      0.000000
75%       23.300000      0.000000
max       37.800000     34.500000

In [48]:
data.describe()

count      1716
unique        6
top       empty
freq        999
dtype: object

In [72]:
data.columns = ['status']

In [81]:
columns = ['status']
total_df = pd.DataFrame(data, columns = columns)

In [82]:
#data.sort_values()
total_df.head()

status
2018-12-13 23:55:00    NaN
2018-11-13 15:05:00    NaN
2019-02-05 18:15:00    NaN
2019-05-02 22:20:00    NaN
2019-01-26 23:45:00    NaN

In [86]:
print(X)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [89]:
print(X[0])

[0, 0, 0, 1, 0, 0, 0, 0.9965277777777778, 1.0, 0.14400000000000002, 0.0]


In [91]:
rf = RandomForestClassifier(n_estimators=200)
rf = rf.fit(X, yempty)

In [92]:
rf.score(X,yempty)

0.9986485915790363

In [93]:
importances = rf.feature_importances_
importances

array([0.012994  , 0.02026308, 0.03039909, 0.01355015, 0.02431624,
       0.03610212, 0.02130511, 0.20201712, 0.34228435, 0.25418743,
       0.04258131])

In [95]:
#sorted(zip(rf.feature_importances_, X.feature_names), reverse=True)

AttributeError: 'list' object has no attribute 'feature_names'

In [99]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, yempty, random_state=42, stratify=yempty)

In [100]:
rf = rf.fit(X_train, y_train)

In [101]:
rf.score(X_train,y_train)

0.999061508718584

In [102]:
rf.score(X_test,y_test)

0.9973536036036036

In [109]:
x_tom = [[0, 0, 0, 1, 0, 0, 0, 0.9965277777777778, 1.0, 0.14400000000000002, 0.0]]


In [110]:
predict = rf.predict(x_tom)

In [111]:
predict

array([0])

In [113]:
predict_test = rf.predict(X_test)

In [119]:
print(predict_test)

[0 0 0 ... 0 0 0]


In [120]:
print(X_test)

[[1, 0, 0, 0, 0, 0, 0, 0.1840277777777778, 0.4166666666666667, 0.312, 0.0], [0, 0, 0, 0, 0, 0, 1, 0.625, 1.0, 0.256, 0.0], [0, 0, 0, 0, 1, 0, 0, 0.6180555555555556, 0.3333333333333333, 0.456, 0.0006666666666666666], [0, 0, 0, 0, 0, 1, 0, 0.6388888888888888, 0.8333333333333334, 0.466, 0.0], [0, 0, 0, 1, 0, 0, 0, 0.4270833333333333, 0.25, 0.14400000000000002, 0.0], [0, 0, 0, 0, 1, 0, 0, 0.3680555555555556, 0.9166666666666666, -0.034, 0.0], [0, 0, 0, 0, 0, 1, 0, 0.3645833333333333, 0.25, 0.055999999999999994, 0.0], [0, 0, 0, 1, 0, 0, 0, 0.59375, 0.3333333333333333, 0.37799999999999995, 0.0], [1, 0, 0, 0, 0, 0, 0, 0.3784722222222222, 0.9166666666666666, 0.212, 0.02], [0, 1, 0, 0, 0, 0, 0, 0.8993055555555556, 0.08333333333333333, 0.266, 0.0], [1, 0, 0, 0, 0, 0, 0, 0.40625, 0.25, 0.134, 0.0], [1, 0, 0, 0, 0, 0, 0, 0.3472222222222222, 0.9166666666666666, 0.122, 0.0], [1, 0, 0, 0, 0, 0, 0, 0.3125, 0.75, 0.478, 0.0], [0, 0, 0, 1, 0, 0, 0, 0.3298611111111111, 0.3333333333333333, 0.17800000000000